In [1]:
import datautils
import camels


Please email feedback to gdex@ucar.edu.



In [5]:
#Get camels data
data = [
     #{'url':'https://gdex.ucar.edu/api/v1/dataset/camels/file/basin_timeseries_v1p2_modelOutput_nldas.zip','filename':'basin_timeseries_v1p2_modelOutput_nldas.zip','bytes':'3766449871','md5Checksum':'32c9973fb13d17a5268ed4affd95fb9a'},
     {'url':'https://gdex.ucar.edu/api/v1/dataset/camels/file/camels_vege.txt','filename':'camels_vege.txt','bytes':'107970','md5Checksum':'f40e843defc1e654a800be9fe5fd5090'},
     {'url':'https://gdex.ucar.edu/api/v1/dataset/camels/file/camels_attributes_v2.0.pdf','filename':'camels_attributes_v2.0.pdf','bytes':'91532','md5Checksum':'77a6c084c798a31fbd05594ee58a90c7'},
     {'url':'https://gdex.ucar.edu/api/v1/dataset/camels/file/camels_topo.txt','filename':'camels_topo.txt','bytes':'38677','md5Checksum':'0f6267838c40b1507b64582433bc0b8e'},
     {'url':'https://gdex.ucar.edu/api/v1/dataset/camels/file/camels_geol.txt','filename':'camels_geol.txt','bytes':'71583','md5Checksum':'f5ce5de53eb1ea2532cda7e3b4813993'},
     {'url':'https://gdex.ucar.edu/api/v1/dataset/camels/file/basin_timeseries_v1p2_metForcing_obsFlow.zip','filename':'basin_timeseries_v1p2_metForcing_obsFlow.zip','bytes':'3406626583','md5Checksum':'8e9a466710e8270b58f01d332a87184f'},
     {'url':'https://gdex.ucar.edu/api/v1/dataset/camels/file/camels_hydro.txt','filename':'camels_hydro.txt','bytes':'122799','md5Checksum':'55ebdeb36c42ee7acdb998229c3edb3a'},
     {'url':'https://gdex.ucar.edu/api/v1/dataset/camels/file/basin_timeseries_v1p2_modelOutput_daymet.zip','filename':'basin_timeseries_v1p2_modelOutput_daymet.zip','bytes':'4207763546','md5Checksum':'f2af624b6277b75b3e410d6a0365591a'},
     {'url':'https://gdex.ucar.edu/api/v1/dataset/camels/file/camels_attributes_v2.0.xlsx','filename':'camels_attributes_v2.0.xlsx','bytes':'16278','md5Checksum':'714c68bd5bb3314ca39b14f9467bd609'},
     {'url':'https://gdex.ucar.edu/api/v1/dataset/camels/file/camels_clim.txt','filename':'camels_clim.txt','bytes':'100673','md5Checksum':'67f22592f3fb72c57df81358ce68458b'},
     {'url':'https://gdex.ucar.edu/api/v1/dataset/camels/file/basin_timeseries_v1p2_modelOutput_maurer.zip','filename':'basin_timeseries_v1p2_modelOutput_maurer.zip','bytes':'3138552670','md5Checksum':'55fb2882136bc2f1e2ce35227396cc1f'},
     {'url':'https://gdex.ucar.edu/api/v1/dataset/camels/file/basin_set_full_res.zip','filename':'basin_set_full_res.zip','bytes':'45179559','md5Checksum':'958fe520f6c4062dbddbbb67cfc28985'},
     {'url':'https://gdex.ucar.edu/api/v1/dataset/camels/file/camels_name.txt','filename':'camels_name.txt','bytes':'30417','md5Checksum':'c96491b32c4df55a31bead7ceca7d64b'},
     {'url':'https://gdex.ucar.edu/api/v1/dataset/camels/file/readme.txt','filename':'readme.txt','bytes':'1704','md5Checksum':'b37d64950e9d4c5c10a8b4ef82bc6219'},
     {'url':'https://gdex.ucar.edu/api/v1/dataset/camels/file/camels_soil.txt','filename':'camels_soil.txt','bytes':'109125','md5Checksum':'8edb46a363a20b466a4b7105ba633767'},
     ]

camels.main(data)

camels_vege.txt downloading: done
camels_vege.txt download successful
camels_attributes_v2.0.pdf downloading: done
camels_attributes_v2.0.pdf download successful
camels_topo.txt downloading: done
camels_topo.txt download successful
camels_geol.txt downloading: done
camels_geol.txt download successful
basin_timeseries_v1p2_metForcing_obsFlow.zip downloading: done
basin_timeseries_v1p2_metForcing_obsFlow.zip download successful
camels_hydro.txt downloading: done
camels_hydro.txt download successful
basin_timeseries_v1p2_modelOutput_daymet.zip downloading: done
basin_timeseries_v1p2_modelOutput_daymet.zip download successful
camels_attributes_v2.0.xlsx downloading: done
camels_attributes_v2.0.xlsx download successful
camels_clim.txt downloading: done
camels_clim.txt download successful
basin_timeseries_v1p2_modelOutput_maurer.zip downloading: done
basin_timeseries_v1p2_modelOutput_maurer.zip download successful
basin_set_full_res.zip downloading: done
basin_set_full_res.zip download succe

Push CAMELs data to AWS to share

In [2]:
#send to s3
import boto3
import os
import pandas as pd

#Set Global Variables
access = pd.read_csv('AWSaccessKeys.csv')

#start session
session = boto3.Session(
    aws_access_key_id=access['Access key ID'][0],
    aws_secret_access_key=access['Secret access key'][0],
)
s3 = session.resource('s3')
#AWS bucket information
bucket_name = 'streamflow-app-data'
bucket = s3.Bucket(bucket_name)



In [3]:
#function to push entire directory to S3
def upload_folder_to_s3(s3, bucket_name, inputDir, s3Path):
    print("Uploading results to s3 initiated...")
    print("Local Source:",inputDir)
    os.system("ls -ltR " + inputDir)

    print("Dest  S3path:",s3Path)

    try:
        for path, subdirs, files in os.walk(inputDir):
            for file in files:
                dest_path = path.replace(inputDir,"")
                __s3file = os.path.normpath(s3Path + '/' + dest_path + '/' + file)
                __local_file = os.path.join(path, file)
                print("upload : ", __local_file, " to Target: ", __s3file, end="")
                #s3bucket.upload_file(__local_file, __s3file)
                s3.meta.client.upload_file(Filename= __local_file, Bucket=bucket_name, Key=f"{s3Path}/{file}")
                print(" ...Success")
    except Exception as e:
        print(" ... Failed!! Quitting Upload!!")
        print(e)
        raise e


In [32]:
home = os.path.expanduser('~')
#push NSM data to AWS
folders =[
        'basin_timeseries_v1p2_metForcing_obsFlow',
        'model_output_daymet',
        'model_output_maurer',
]
for folder in folders:
    print(folder)
    # folder = "nwm"
    s3Path = f"CAMELS/data/{folder}"
    localpath = f"{home}/lstm_for_GSL/data/{folder}"
    upload_folder_to_s3(s3, bucket_name, localpath, s3Path)

Uploading results to s3 initiated...
Local Source: /home/rjohnson18/lstm_for_GSL/data/model_output_nldas
/home/rjohnson18/lstm_for_GSL/data/model_output_nldas:
total 4
drwxr-xr-x 3 rjohnson18 rjohnson18 4096 Nov  6  2017 model_output

/home/rjohnson18/lstm_for_GSL/data/model_output_nldas/model_output:
total 4
drwxr-xr-x 3 rjohnson18 rjohnson18 4096 Nov  6  2017 flow_timeseries

/home/rjohnson18/lstm_for_GSL/data/model_output_nldas/model_output/flow_timeseries:
total 4
drwxr-xr-x 20 rjohnson18 rjohnson18 4096 Mar  8  2016 nldas

/home/rjohnson18/lstm_for_GSL/data/model_output_nldas/model_output/flow_timeseries/nldas:
total 1320
drwxr-xr-x 2 rjohnson18 rjohnson18 163840 Jan 26  2015 17
drwxr-xr-x 2 rjohnson18 rjohnson18  69632 Jan 26  2015 18
drwxr-xr-x 2 rjohnson18 rjohnson18  36864 Jan 26  2015 16
drwxr-xr-x 2 rjohnson18 rjohnson18  16384 Jan 26  2015 13
drwxr-xr-x 2 rjohnson18 rjohnson18  36864 Jan 26  2015 14
drwxr-xr-x 2 rjohnson18 rjohnson18  36864 Jan 26  2015 15
drwxr-xr-x 2 rjoh

In [6]:
home = os.path.expanduser('~')

#push NSM data to AWS
folders =[
        'camels_attributes_v2.0/model_output_maurer/model_output/flow_timeseries/maurer/18/'
]
for folder in folders:
    print(folder)
    # folder = "nwm"
    s3Path = f"CAMELS/data/{folder}"
    localpath = f"{home}/lstm_for_GSL/data/{folder}"
    upload_folder_to_s3(s3, bucket_name, localpath, s3Path)

camels_attributes_v2.0/model_output_maurer/model_output/flow_timeseries/maurer/18/
Uploading results to s3 initiated...
Local Source: /home/rjohnson18/lstm_for_GSL/data/camels_attributes_v2.0/model_output_maurer/model_output/flow_timeseries/maurer/18/
/home/rjohnson18/lstm_for_GSL/data/camels_attributes_v2.0/model_output_maurer/model_output/flow_timeseries/maurer/18/:
total 791480
-rw-r--r-- 1 rjohnson18 rjohnson18  887570 Mar 11  2016 11528700_48_model_soil_state_output.txt
-rw-r--r-- 1 rjohnson18 rjohnson18 1135256 Mar 11  2016 11528700_59_model_output.txt
-rw-r--r-- 1 rjohnson18 rjohnson18  887570 Mar 11  2016 11528700_59_model_soil_state_output.txt
-rw-r--r-- 1 rjohnson18 rjohnson18 1135256 Mar 11  2016 11528700_66_model_output.txt
-rw-r--r-- 1 rjohnson18 rjohnson18  888098 Mar 11  2016 11528700_66_model_soil_state_output.txt
-rw-r--r-- 1 rjohnson18 rjohnson18 1135256 Mar 11  2016 11528700_72_model_output.txt
-rw-r--r-- 1 rjohnson18 rjohnson18  887570 Mar 11  2016 11528700_72_model